SO 
Here is how I'm gonna do this
as a first try, without any preprocessing, simply combine all the data into a single
dataframe, regardless of threshold, just to nail down how the data needs to be structured

one by one, read in the csv files, creating one line in the data frame for every 30 frames
then write the identity in terms of video, bramble-or-rose, startframe, id, extracted body-length, as the 
first 5 elements in the row. The 6th entry is then the size class, so we can use that as a
label. without any smoothing, angles, or speeds, the shape of the data-frame will then be

(n, 30 * num_key_points + 6)

to run dimensionality reduction on that data, simply repeat the setup above:

In [1]:
import cv2
import pickle
import os
from tqdm import tqdm
import numpy as np
import sys
import pandas as pd
from umap import UMAP
from sklearn.manifold import TSNE
import plotly.express as px

sys.path.append("..")  # Adds higher directory to python modules path.

# now for the file management functions
from evaluation.Antrax_base import import_tracks, display_video, compose_video_with_overlay


def find_class(array, value):
    array_np = np.asarray(array)
    idx = (np.abs(array_np - value)).argmin()
    nearest_class = array_np[idx]
    pred_class = array.index(nearest_class)
    return pred_class


def clean_array(array, strip_NaN=True, strip_zero=True):
    array_np = np.asarray(array)
    if strip_NaN:
        array_np = array_np[np.logical_not(np.isnan(array_np))]
    if strip_zero:
        array_np = array_np[np.nonzero(array_np)]
    return array_np


input_video = "I:/EAEAAO/FOOTAGE/2019-08-03/2019-08-03_bramble-left.avi"
input_tracks = "I:/EAEAAO/Tracking/OUTPUT_TRACKS/2019-08-03_bramble-left"
input_poses = "I:/EAEAAO/POSES/2019-08-03_bramble-left"
input_file_order = "I:/EAEAAO/jobscripts/EAEAAO_batch_pose.pbs.o8454338.16"

start_frame = 0
end_frame = 1000

# read in order file and re-order tracks, so they correspond to their corresponding poses
file_order = open(input_file_order, 'r')
order_raw = file_order.readlines()

# Strips the newline character
order = []
for line in order_raw:
    if line.split("  with ")[0][-4:] == ".csv":
        order.append(line.split(" ")[2])
        print(order[-1])

# now we can load the captured video file and display it
cap = cv2.VideoCapture(input_video)

# check the number of frames of the imported video file
numFramesMax = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
print("The imported clip:", input_video, "has a total of", numFramesMax, "frames.\n")

tracks = import_tracks(input_tracks, numFramesMax,
                       export=False,
                       min_track_length=100,
                       strip_tail_frames=50,
                       min_movement_px=50,
                       custom_order=order)

# The following function is used to display the tracks you imported.
# You can press "q" while hovering over the displayed video to exit.
print("\nDisplaying tracks loaded from:", input_tracks)
tracked_frames = len(tracks[0])

# next load all poses and append them to a list
all_poses = []
all_sizes = []
all_pose_ids = []

px_to_mm_POSE = 16.0848
px_to_mm_TRACK = 6.8628

2019-08-03_bramble-left_track_634.csv
2019-08-03_bramble-left_track_153.csv
2019-08-03_bramble-left_track_979.csv
2019-08-03_bramble-left_track_417.csv
2019-08-03_bramble-left_track_1714.csv
2019-08-03_bramble-left_track_317.csv
2019-08-03_bramble-left_track_845.csv
2019-08-03_bramble-left_track_950.csv
2019-08-03_bramble-left_track_1475.csv
2019-08-03_bramble-left_track_1057.csv
2019-08-03_bramble-left_track_782.csv
2019-08-03_bramble-left_track_732.csv
2019-08-03_bramble-left_track_723.csv
2019-08-03_bramble-left_track_684.csv
2019-08-03_bramble-left_track_1044.csv
2019-08-03_bramble-left_track_616.csv
2019-08-03_bramble-left_track_639.csv
2019-08-03_bramble-left_track_1004.csv
2019-08-03_bramble-left_track_1247.csv
2019-08-03_bramble-left_track_1440.csv
2019-08-03_bramble-left_track_1154.csv
2019-08-03_bramble-left_track_43.csv
2019-08-03_bramble-left_track_1638.csv
2019-08-03_bramble-left_track_751.csv
2019-08-03_bramble-left_track_1294.csv
2019-08-03_bramble-left_track_300.csv
201

In [2]:
for r, d, f in os.walk(input_poses):
    for file in f:
        print("Loading pose from", file)
        df = pd.read_csv(os.path.join(input_poses, file), delimiter=',', header=[0, 1, 2])

        x_diff = df["OmniTrax"]["b_t"]["x"].to_numpy() - df["OmniTrax"]["b_a_5"]["x"].to_numpy()
        y_diff = df["OmniTrax"]["b_t"]["y"].to_numpy() - df["OmniTrax"]["b_a_5"]["y"].to_numpy()

        lengths = np.sqrt(np.square(x_diff) + np.square(y_diff))
        median_length = np.round(np.median(lengths) / px_to_mm_POSE, 2)

        # now, use the appropriate class ID
        all_sizes.append(find_class([3, 4, 5, 6, 7], median_length))
        all_poses.append(df.to_numpy())
        all_pose_ids.append(int(file.split("_")[-1][:-4]))

all_poses_sorted = [pose for _, pose in sorted(zip(all_pose_ids, all_poses))]
all_sizes_sorted = [size for _, size in sorted(zip(all_pose_ids, all_sizes))]

Loading pose from 2019-08-03_bramble-left_POSE_0.csv
Loading pose from 2019-08-03_bramble-left_POSE_1.csv
Loading pose from 2019-08-03_bramble-left_POSE_10.csv
Loading pose from 2019-08-03_bramble-left_POSE_100.csv
Loading pose from 2019-08-03_bramble-left_POSE_1000.csv
Loading pose from 2019-08-03_bramble-left_POSE_1001.csv
Loading pose from 2019-08-03_bramble-left_POSE_1002.csv
Loading pose from 2019-08-03_bramble-left_POSE_1003.csv
Loading pose from 2019-08-03_bramble-left_POSE_1004.csv
Loading pose from 2019-08-03_bramble-left_POSE_1005.csv
Loading pose from 2019-08-03_bramble-left_POSE_1006.csv
Loading pose from 2019-08-03_bramble-left_POSE_1007.csv
Loading pose from 2019-08-03_bramble-left_POSE_1008.csv
Loading pose from 2019-08-03_bramble-left_POSE_1009.csv
Loading pose from 2019-08-03_bramble-left_POSE_101.csv
Loading pose from 2019-08-03_bramble-left_POSE_1010.csv
Loading pose from 2019-08-03_bramble-left_POSE_1011.csv
Loading pose from 2019-08-03_bramble-left_POSE_1012.csv
Lo

### first things first - keep it simple and start with a minimal viable approach
get this to run in the simplest configuration described above
then we roughly know how long this takes to compute, the memory and cpu requirements
optimise shit only if ABSOLUTELY necessary

using the completely unprossed data above this will likely yield what is essentially a
glorified size estimator -> as the main differences in the values will be the distances
to the image centre, providing the animal sizes as labels should be a good start

additionally, we can go a tiny step further by also **addind the food-source** as a label
so we can already have two kinds of clustering outputs available

___________________________________

now, to add more information and to make this a little more size invariant, some basic filtering
is required. We do all of this in order of necessity/complexity and stop as soon as the picture is comprehensive or we run out of time, whichever comes first

### clean trajectories
now for some cleanup:
- first, exclude keypoints with below threshold confidence EXCEPT for the first frame, so we always have one set of values to begin with
- next, "fill in the blanks", meaning for every sub-treshold value, use the last and the next valid state. So, for the same reason as above, the last frame is also treated as a "keep all values regardless of threshold thing"
- once values are cleaned and interpolated, smooth the trajectories with the functions already implemented (convolve, or whichever one gave good speeds back)
- now, centre the movement at b_t and align with b_a_1, then compute the new locations for all points
- now, normalise the location of all points, by the body length, so get the average distance between b_t and align with b_a_1 across all frames and divide all keypoints by that value

Re-run clustering if you're keen. But mostly, just try to replay the resulting chunks to see if this has done what you thought it should. 

### additional features
This is gonna be relatively simple. What we care about should be speeds and key-point relationships over time. Think about this for a moment. If we go for angles only, that also means less centering and normalisation stuff required!
- angles: get the 2D angles between key body parts in the skeleton (so legs and stuff)
- angular-rates: get the change in angles over time in deg/sec
-> re-use the OmniTrax code here! It doesn't matter if it's not perfect, as long as the feautures are consistent!

That should be enough processing!

## re-run
Trajectories are cleaned, post-processing is done, additional features are extracted resulting in a new feature vector of the shape

(n, 30 * num_key_points + 60 * num_angles + 5)

assuming we have about 20 relevant angles and thus 19 angle change rates that leaves us with about ~2500 features. We can then decide whether we want to get rid of bodypart locations entirely and only look at angles, but that can be decided once its implemented. Less is always an option.

COol coOl cool. 
And just like that we'd have our own behavioural clustering.

And now for someting important:

**This is only about embedding stuff. It's easy to train a classifier on top of this for real-time action recognition and no important novelty lies in that. Saying that that can be done is enough. Use a fucking umap if you are bored. You'll have all you need, so don't make interpreting beautiful results harder.**

In [ ]:
# now loop over all pose elements and produce the format stated above
# "video", "material", "startframe", "id", "extracted body-length"

material = input_poses.split("_")[-1].split("-")[0]
clip_length = 25 # meaning, we consider each 30-frame istance as one beahvioural sample
out_list = []
centre_poses = True # if true, centres poses at b_t
align_poses = True # if true, aligns all poses with b_t -> b_a_1 being the middle
display = False

stop_early = True

compute_size_class_for_each_action = True

import math

def rotate(p, origin=(0, 0), degrees=0):
    angle = np.deg2rad(degrees)
    R = np.array([[np.cos(angle), -np.sin(angle)],
                  [np.sin(angle),  np.cos(angle)]])
    o = np.atleast_2d(origin)
    p = np.atleast_2d(p)
    return np.squeeze((R @ (p.T-o.T) + o.T).T)


def get_derivative(tracks, time_step=1 / 30, verbose=False):
    tracks_der = np.zeros([tracks.shape[0], int((tracks.shape[1] - 1) / 2)])
    # convert tracks to float array
    tracks_der = tracks_der.astype(float)

    num_tracks = int((tracks.shape[1] - 1) / 2)
    num_timeSteps = tracks.shape[0]

    if verbose:
        print("Computing derivative for", num_tracks, "tracks...")

    for t in range(num_timeSteps - 1):
        # then retrieve all track centres at the given frame
        track_centres = tracks[t, 1:]
        track_centres_non_zero_ids = np.nonzero(track_centres)[0][::2]

        if len(track_centres_non_zero_ids) != 0:

            for track_orig in track_centres_non_zero_ids:
                track = int((track_orig + 1) / 2)

                # check that the next value is no zero

                if tracks[t + 1, track * 2 + 1] == 0 or tracks[t + 1, track * 2 + 2] == 0:
                    continue

                tracks_der[t, track] = np.sqrt((tracks[t + 1, track * 2 + 1] -
                                                tracks[t, track * 2 + 1]) ** 2 +
                                               (tracks[t + 1, track * 2 + 2] -
                                                tracks[t, track * 2 + 2]) ** 2) / time_step

    return tracks_der

def get_derivative_angles(tracks, time_step=1 / 30, verbose=False):
    tracks = tracks[:,1:] # strip frame counter
    tracks_der = np.zeros((tracks.shape[0] - 1, tracks.shape[1]))
    # convert tracks to float array
    tracks_der = tracks_der.astype(float)

    num_tracks = tracks.shape[1]
    num_timeSteps = tracks.shape[0]

    if verbose:
        print("Computing derivative for", num_tracks, "angles...")

    for t in range(num_timeSteps - 1):
        # then retrieve all track centres at the given frame
        
        for track in range(num_tracks):
            # check that the next value is non-zero

            if tracks[t + 1, track] == 0:
                continue

            tracks_der[t, track] = (tracks[t + 1, track] - tracks[t, track])  / time_step

    return tracks_der


def apply_moving_average(tracks, samples=3, padding_mode='valid',verbose=False):
    tracks_ma = np.copy(tracks)
    tracks_ma.astype(float)
    num_tracks = int((tracks.shape[1] - 1) / 2)

    if verbose:
        print("Applying moving average of size", samples, "to", num_tracks, "tracks...")
    for t in range(num_tracks):
        # apply smoothing only to areas where tracked subject is in view
        # therefore, all zero entries must be ignored
        track_temp_x = tracks[:, t * 2 + 1]
        track_temp_y = tracks[:, t * 2 + 2]

        nonzeroind = np.nonzero(track_temp_x)[0]

        # the following code is bad and slow. But I don't care. There is a strange artifact in some exported tracks
        # where there are sudden un-connected coordinates appearing outside the tracked area. So we find those and
        # remove them. No matter the (compute) cost.

        rm_ind = []

        for ind, f in enumerate(nonzeroind):
            if 0 < f < len(tracks) - 1:
                if tracks[f, t * 2 + 1] != 0 and tracks[f - 1, t * 2 + 1] == 0 and tracks[f + 1, t * 2 + 1] == 0:
                    rm_ind.append(ind)

        nonzeroind = np.delete(nonzeroind, rm_ind)

        track_x = np.convolve(track_temp_x[nonzeroind[0]:nonzeroind[-1] - samples], np.ones(samples) / samples,
                              mode=padding_mode)
        track_y = np.convolve(track_temp_y[nonzeroind[0]:nonzeroind[-1] - samples], np.ones(samples) / samples,
                              mode=padding_mode)

        tracks_ma[nonzeroind[0] + math.floor(samples / 2):nonzeroind[-1] - math.ceil(samples / 2) - samples + 1,
        t * 2 + 1] = track_x
        tracks_ma[nonzeroind[0] + math.floor(samples / 2):nonzeroind[-1] - math.ceil(samples / 2) - samples + 1,
        t * 2 + 2] = track_y

        # add back zeros
    return tracks_ma


track_id = -1 # we can now iterate through tracks consecutively as we reordered them based on their associated poses

for id, pose, size in tqdm(zip(order, all_poses_sorted,all_sizes_sorted), total=(len(order))):
    track_id += 1
    id_val = int(id.split("_")[-1][:-4])
    if stop_early:
        if track_id == 100:
            break
    for instances in range(math.floor(int(len(pose)/clip_length))):
        skip_instance = False
        
        num_features = pose[int(instances*clip_length) + 1:int(instances*clip_length) + 1 + clip_length,1:]
        num_features = int(num_features.shape[1] / 3)

        #drop_thresh_idx = [i*3 + 2 for i in range(num_features)]
        
        frame_start = int(pose[int(instances*clip_length) + 1,0])
        # now create feature vector from instance
        features = pose[int(instances*clip_length) + 1:int(instances*clip_length) + 1 + clip_length,1:]

        out_features = np.zeros(num_features*2*clip_length)
        out_features_angles = np.zeros(9*clip_length) # abdomen, legs, antennae

        loc_counter = 0

        for frame in range(clip_length):
            if display:
                blank_image = np.zeros((300, 300, 3), np.uint8)

            try:
                avg_front = np.mean([features[frame][0:2],features[frame][126:128]],axis=0)
                avg_back = np.mean([features[frame][3:5],features[frame][6:8],features[frame][9:11],features[frame][12:14]],axis=0)
                body_orientation = np.arccos(np.dot([0,1],avg_back - avg_front) / 
                                            (np.linalg.norm([0,1]) * np.linalg.norm(avg_back - avg_front)))
            except IndexError:
                skip_instance = True
                break
            
            for p in range(num_features):
                if features[frame][p * 3 + 2] >= 0.5:
                    point = features[frame][p * 3:p * 3 + 2]

                    if centre_poses:
                        point = point - avg_front + [150,120]

                    if align_poses:
                        point = rotate(point, [150,120], degrees=body_orientation * 180/np.pi)

                    #print(loc_counter)
                    out_features[loc_counter:loc_counter + 2] = point

                    if display:
                        blank_image = cv2.circle(blank_image, (int(point[0]), int(point[1])),
                                                 3,
                                                 (int(255 * p / num_features),
                                                  int(255 - 255 * p / num_features), 200),
                                                 -1)
                loc_counter += 2

            # get joint angles and use the weighted mean of each leg for more robust estimates
            # the following is hard coded to get locations of key body parts but that's okay for now. It works for insects.
            loc_antennae_l = np.reshape(features[frame][138:147],(-1,3))
            loc_antennae_r = np.reshape(features[frame][129:138],(-1,3))
            loc_leg_l_1 = np.reshape(features[frame][72:90],(-1,3))
            loc_leg_l_2 = np.reshape(features[frame][90:108],(-1,3))
            loc_leg_l_3 = np.reshape(features[frame][108:126],(-1,3))
            loc_leg_r_1 = np.reshape(features[frame][18:36],(-1,3))
            loc_leg_r_2 = np.reshape(features[frame][36:54],(-1,3))
            loc_leg_r_3 = np.reshape(features[frame][54:72],(-1,3))
            loc_abdomen = np.reshape(features[frame][3:18],(-1,3))

            avg_loc_antennae_l = np.average(loc_antennae_l[:,:2],axis=0, weights=np.transpose([loc_antennae_l[:,2],loc_antennae_l[:,2]]))
            avg_loc_antennae_r = np.average(loc_antennae_r[:,:2],axis=0, weights=np.transpose([loc_antennae_r[:,2],loc_antennae_r[:,2]]))
            avg_loc_leg_l_1 = np.average(loc_leg_l_1[:,:2],axis=0, weights=np.transpose([loc_leg_l_1[:,2],loc_leg_l_1[:,2]]))
            avg_loc_leg_l_2 = np.average(loc_leg_l_2[:,:2],axis=0, weights=np.transpose([loc_leg_l_2[:,2],loc_leg_l_2[:,2]]))
            avg_loc_leg_l_3 = np.average(loc_leg_l_3[:,:2],axis=0, weights=np.transpose([loc_leg_l_3[:,2],loc_leg_l_3[:,2]]))
            avg_loc_leg_r_1 = np.average(loc_leg_r_1[:,:2],axis=0, weights=np.transpose([loc_leg_r_1[:,2],loc_leg_r_1[:,2]]))
            avg_loc_leg_r_2 = np.average(loc_leg_r_2[:,:2],axis=0, weights=np.transpose([loc_leg_r_2[:,2],loc_leg_r_2[:,2]]))
            avg_loc_leg_r_3 = np.average(loc_leg_r_3[:,:2],axis=0, weights=np.transpose([loc_leg_r_3[:,2],loc_leg_r_3[:,2]]))
            avg_loc_abdomen = np.average(loc_abdomen[:,:2],axis=0, weights=np.transpose([loc_abdomen[:,2],loc_abdomen[:,2]]))

            combined_poses = [[loc_antennae_l, avg_loc_antennae_l],
                              [loc_antennae_r, avg_loc_antennae_r],
                              [loc_leg_l_1, avg_loc_leg_l_1],
                              [loc_leg_l_2, avg_loc_leg_l_2],
                              [loc_leg_l_3, avg_loc_leg_l_3],
                              [loc_leg_r_1, avg_loc_leg_r_1],
                              [loc_leg_r_2, avg_loc_leg_r_2],
                              [loc_leg_r_3, avg_loc_leg_r_3],
                              [loc_abdomen, avg_loc_abdomen]]

            unit_vector_body_axis = [0, 1]
            
            for c, comb in enumerate(combined_poses):
                point = [comb[1][0],comb[1][1]]
                if centre_poses:
                        point = point - avg_front + [150,120]

                if align_poses:
                    point = rotate(point, [150,120], degrees=body_orientation * 180/np.pi)
                    
                bone_vector = [comb[1][0] - comb[0][0][0], comb[1][1] - comb[0][0][1]]
                unit_vector_bone_vector = bone_vector / np.linalg.norm(bone_vector)
                dot_product = np.dot(unit_vector_body_axis, unit_vector_bone_vector)
                out_features_angles[frame * len(combined_poses) + c] = (180/np.pi) * np.arccos(np.clip(dot_product, -1.0, 1.0))        
                
                if display:                      
                    blank_image = cv2.circle(blank_image, (int(point[0]), int(point[1])),
                                             5,
                                             (255, 255 , 255),
                                             -1)

            if display:
                cv2.imshow("test", blank_image)
                cv2.waitKey(1)

        # get std for each point, if avg std is too high, discard, use weight means
        check_features = out_features.reshape(clip_length,num_features,2)
        check_features_std = np.std(check_features,axis=0)
        mean_std = np.nanmean(check_features_std)

        if mean_std >= 45:
            skip_instance = True
    
        if skip_instance:
            continue


        if compute_size_class_for_each_action:
            
            x_diff = features[:,0] - features[:,15] #  b_tX -  b_a_5X
            y_diff = features[:,1] - features[:,16] #  b_tY -  b_a_5Y
    
            lengths = np.sqrt(np.square(x_diff) + np.square(y_diff))
            median_length = np.round(np.median(lengths) / px_to_mm_POSE, 2)
    
            # now, use the appropriate class ID
            size = find_class([3, 4, 5, 6, 7], median_length)

        # get speed from assocaited tracks
        temp_tracks = tracks[frame_start:frame_start + clip_length, track_id*2 + 1: track_id*2 + 3]
        temp_track_frames = np.arange(clip_length)
        temp_tracks = np.stack((temp_track_frames,temp_tracks[:,0],temp_tracks[:,1]), axis= 1)
        tracks_MA = apply_moving_average(temp_tracks, 5)
        tracks_speed = get_derivative(tracks_MA, time_step=1 / 25)
        speed = max(np.mean(tracks_speed[np.nonzero(tracks_speed)], axis=0),0.001) / px_to_mm_TRACK

        # get angular rates from computed angles
        temp_angle_frames = np.arange(clip_length)
        temp_angles = np.column_stack((temp_angle_frames,out_features_angles.reshape((clip_length,9))))
        temp_angles_MA = apply_moving_average(temp_angles, 5)
        angular_velocity = get_derivative_angles(temp_angles_MA, time_step=1 / 25)
        angular_velocity = angular_velocity.flatten()
            
        # create list of all features, starting with static features
        temp_list = [os.path.basename(input_poses), material, frame_start, id_val, speed, size]

        # and extending the feature vector with dynamic features (pose, angles, angular rates)
        temp_list.extend(out_features.tolist())
        temp_list.extend(out_features_angles.tolist())
        temp_list.extend(angular_velocity.tolist())
        
        out_list.append(temp_list)

cv2.destroyAllWindows()

In [144]:
header = ["video", "material", "startframe", "id", "speed", "size_class"]
feature_header = ["raw_pose_" + str(i) for i in range(int(num_features*2*clip_length))]
feature_angle_header = ["angles_" + str(i) for i in range(9*clip_length)]
feature_angle_vel_header = ["angular_velocity_" + str(i) for i in range(9*(clip_length-1))]

header.extend(feature_header)
header.extend(feature_angle_header)
header.extend(feature_angle_vel_header)

df_ant_poses = pd.DataFrame(out_list)

df_ant_poses.columns = header
# fill NaNs with zeros to keep things clean
df_ant_poses = df_ant_poses.fillna(0)

out_df_file_name = str(os.path.basename(input_poses)) + "_POSE_FEATURE_DICT.pkl"
df_ant_poses.to_pickle(os.path.join("EXTRACTED_POSE_FEATURE_VECTORS", out_df_file_name)) 

features = df_ant_poses.loc[:, 'raw_pose_0':] # use all entries and exclude labels
labels =  df_ant_poses.loc[:, :"size_class"]

norm_features = (features-features.min())/(features.max()-features.min())

In [145]:
print("extracted feature vector contains",norm_features.shape[0],"instances and", norm_features.shape[1], "features")
norm_features

extracted feature vector contains 4680 instances and 2891 features


raw_pose_0  raw_pose_1  raw_pose_2  raw_pose_3  raw_pose_4  raw_pose_5  \
0       0.724953    0.638406    0.572293    0.474765    0.576779    0.488389   
1       0.736914    0.618210    0.603243    0.494162    0.600610    0.505918   
2       0.000000    0.000000    0.575050    0.473946    0.572653    0.487143   
3       0.730287    0.619349    0.578251    0.458796    0.573368    0.466912   
4       0.738632    0.605896    0.656611    0.408308    0.676771    0.404044   
...          ...         ...         ...         ...         ...         ...   
4675    0.727745    0.640099    0.575162    0.460432    0.573900    0.473240   
4676    0.728143    0.639367    0.570935    0.476093    0.572848    0.486718   
4677    0.727617    0.642163    0.574180    0.476321    0.574664    0.488611   
4678    0.737061    0.643280    0.572700    0.481775    0.576580    0.500331   
4679    0.729917    0.641168    0.577150    0.480443    0.581825    0.499019   

      raw_pose_6  raw_pose_7  raw_pose_8  raw_pose_9  ...  \
0       0.401868    0.533323    0.459432    0.609463  ...   
1       0.419046    0.541177    0.474566    0.602213  ...   
2       0.398145    0.533286    0.463926    0.603078  ...   
3       0.399159    0.508073    0.460214    0.574996  ...   
4       0.501669    0.435552    0.556589    0.500353  ...   
...          ...         ...         ...         ...  ...   
4675    0.401379    0.511648    0.459984    0.577180  ...   
4676    0.405380    0.528562    0.460114    0.598320  ...   
4677    0.404300    0.533510    0.457457    0.603009  ...   
4678    0.400773    0.536435    0.460286    0.607583  ...   
4679    0.397975    0.542039    0.455798    0.617648  ...   

      angular_velocity_206  angular_velocity_207  angular_velocity_208  \
0                 0.484599              0.487405              0.513414   
1                 0.476767              0.435181              0.774197   
2                 0.496046              0.596477              0.538789   
3                 0.481102              0.493763              0.834445   
4                 0.468581              0.510742              0.496821   
...                    ...                   ...                   ...   
4675              0.451607              0.516822              0.512120   
4676              0.475276              0.473000              0.402768   
4677              0.476644              0.475884              0.572587   
4678              0.490670              0.442840              0.528328   
4679              0.475588              0.150946              0.480451   

      angular_velocity_209  angular_velocity_210  angular_velocity_211  \
0                 0.487552              0.492044              0.530479   
1                 0.596473              0.563895              0.827748   
2                 0.456542              0.565912              0.531176   
3                 0.314317              0.324874              0.636760   
4                 0.508343              0.600238              0.613671   
...                    ...                   ...                   ...   
4675              0.469220              0.417233              0.507615   
4676              0.553487              0.515973              0.616311   
4677              0.582735              0.524567              0.494411   
4678              0.504440              0.515646              0.504432   
4679              0.291176              0.607158              0.516913   

      angular_velocity_212  angular_velocity_213  angular_velocity_214  \
0                 0.650489              0.489355              0.420877   
1                 0.553959              0.921261              0.923295   
2                 0.979982              0.912883              0.639775   
3                 0.688493              0.664628              0.636770   
4                 0.635567              0.456860              0.421786   
...                    ...                   ...                   ...   
4675            

In [146]:
# as a test, run a 2D tSNE
tsne = TSNE(n_components=2, random_state=0, init="pca", learning_rate="auto", perplexity=50)
projections = tsne.fit_transform(norm_features)

In [147]:
# now take the produced embedding and plot with different colour overlays to group by class, speed, or material
fig_size = px.scatter(
    projections, x=0, y=1,
    color=df_ant_poses.size_class, labels={'color': 'size_class'},
    width=600, height=500) 

fig_size.write_image("tSNE_fig_size.svg")

fig_speed = px.scatter(
    projections, x=0, y=1,
    color=df_ant_poses.speed, labels={'color': 'speed'},
    width=600, height=500) 

fig_speed.write_image("tSNE_fig_speed.svg")

fig_material = px.scatter(
    projections, x=0, y=1,
    color=df_ant_poses.material, labels={'color': 'material'},
    width=600, height=500) 

fig_material.write_image("tSNE_fig_material.svg")

fig_size.show()
fig_speed.show()
fig_material.show()

In [149]:
umap_2d = UMAP(n_components=2, init='random')#, random_state=0)
umap_3d = UMAP(n_components=3, init='random')#, random_state=0)

proj_2d = umap_2d.fit_transform(norm_features)
proj_3d = umap_3d.fit_transform(norm_features)

fig_size_2d = px.scatter(
    proj_2d, x=0, y=1,
    color=df_ant_poses.size_class, labels={'color': 'size_class'},
    width=600, height=500
)

fig_size_3d = px.scatter_3d(
    proj_3d, x=0, y=1, z=2,
    color=df_ant_poses.size_class, labels={'color': 'size_class'},
    width=600, height=500
)
fig_size_3d.update_traces(marker_size=5)


fig_speed_2d = px.scatter(
    proj_2d, x=0, y=1,
    color=df_ant_poses.speed, labels={'color': 'speed'},
    width=600, height=500
)

fig_speed_3d = px.scatter_3d(
    proj_3d, x=0, y=1, z=2,
    color=df_ant_poses.speed, labels={'color': 'speed'},
    width=600, height=500
)
fig_speed_3d.update_traces(marker_size=5)

fig_size_2d.show()
fig_size_3d.show()

fig_speed_2d.show()
fig_speed_3d.show()